In [54]:
# TFG - Inteligencia Artificial
# Maseda Tarin, Miguel
# 2018


import scipy.io # import .mat
import time
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
import seaborn as sns


from skfeature.function.statistical_based import f_score
from skfeature.function.information_theoretical_based import MRMR

from mlxtend.feature_selection import SequentialFeatureSelector as SFS

from sklearn.model_selection import cross_validate
from sklearn.model_selection import StratifiedShuffleSplit
from sklearn.model_selection import StratifiedKFold

from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC

from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import confusion_matrix


from datetime import timedelta

In [40]:
def printBestResult_02(myArray,ml):
    bestResult = []
    for i in range(0,len(myArray)):
        maxAcc = myArray[i][ml][0]['Test'].idxmax()
        maxAccuracy = myArray[i][ml][0]['Test'][maxAcc]
        bestResult.append(myArray[i][0])
        bestResult.append(maxAccuracy)
    bestResult = np.reshape(bestResult,(-1,2))
    bestResult = pd.DataFrame(bestResult)
    bestResult.columns = ['idx','Accuracy']
    bestResult[['Accuracy']] = bestResult[['Accuracy']].apply(pd.to_numeric)
    best_accuracy = bestResult['Accuracy'].idxmax()
    print('- Max Accuracy: ' + str(bestResult.loc[best_accuracy,'Accuracy']) + ' pos: ' + str(best_accuracy))
    return bestResult

In [29]:
def reshapeArray(myArray):
    myArray = np.reshape(myArray,(-1,4))
    myDf = pd.DataFrame(myArray)
    myDf.columns=['idx','KNN','DTC','SVC']
    myDf[['KNN','DTC','SVC']] = myDf[['KNN','DTC','SVC']].apply(pd.to_numeric)
    myDf2 = myDf[['KNN','DTC','SVC']]
    return myDf,myDf2

In [30]:
def bestDf(df):
    KNN = df['KNN'].idxmax()
    DTC = df['DTC'].idxmax()
    SVC = df['SVC'].idxmax()

    idxKNN = df.loc[testKNN,'idx']
    idxDTC = df.loc[testDTC,'idx']
    idxSVC = df.loc[testSVC,'idx']

    return idxKNN,idxDTC,idxSVC

In [25]:
def selectBestForward(num_feat,sbs_model,X,y,idx,models):
    bestForward = []
    X_train = X[:,idx]
    i = 1
    while i < num_feat:
        startTime = time.time()
        svm_b = SFS(sbs_model,
            k_features=i,
            forward=False,
            floating=True,
            verbose=0,
            scoring='accuracy',
            cv=0,
            n_jobs=1)
        svm_b = svm_b.fit(X_train,y,custom_feature_names=idx)
        idx_b = svm_b.k_feature_names_
        endTimeSFS = time.time()
        timeUsedSFS = timedelta(seconds=endTimeSFS-startTime)
        print('- Time used in SBS iteration ' + str(i) +': ' + str(timeUsedSFS))
        print(str(len(idx_b)))
        bestForward.append(idx_b)
        X_sbs = X[:,idx_b]
        for model in models:
            cv = cross_validate(model,X_sbs,y,cv=5,return_train_score=True)
            bestForward.append(cv['test_score'].mean())
        i += 1
    return bestForward


In [26]:
def selectBestBackward(num_feat,sbs_model,X,y,idx,models):
    bestBackward = []
    X_train = X[:,idx]
    i = 0
    while i < num_feat:
        startTime = time.time()
        svm_b = SFS(sbs_model,
            k_features=num_feat-i,
            forward=False,
            floating=True,
            verbose=0,
            scoring='accuracy',
            cv=0,
            n_jobs=1)
        svm_b = svm_b.fit(X_train,y,custom_feature_names=idx)
        idx_b = svm_b.k_feature_names_
        endTimeSFS = time.time()
        timeUsedSFS = timedelta(seconds=endTimeSFS-startTime)
        print('- Time used in SBS iteration ' + str(i) +': ' + str(timeUsedSFS))
        print(str(len(idx_b)))
        bestBackward.append(idx_b)
        X_sbs = X[:,idx_b]
        for model in models:
            cv = cross_validate(model,X_sbs,y,cv=5,return_train_score=True)
            bestBackward.append(cv['test_score'].mean())
        i += 1
    return bestBackward


In [51]:
def selectBestBackward2(num_feat,sbs_model,X,y,idx,models,limite):
    X_train = X[:,idx]
    i = 0
    parar = False
    result2 = 0
    while i < num_feat and parar==False:
        startTime = time.time()
        svm_b = SFS(sbs_model,
            k_features=num_feat-i,
            forward=False,
            floating=True,
            verbose=0,
            scoring='accuracy',
            cv=0,
            n_jobs=1)
        svm_b = svm_b.fit(X_train,y,custom_feature_names=idx)
        idx_b = svm_b.k_feature_names_
        endTimeSFS = time.time()
        timeUsedSFS = timedelta(seconds=endTimeSFS-startTime)
        print('- Time used in SBS iteration ' + str(i) +': ' + str(timeUsedSFS))
        print(str(len(idx_b)))
        X_sbs = X[:,idx_b]
        for model in models:
            cv = cross_validate(model,X_sbs,y,cv=5,return_train_score=True)
            result = cv['test_score'].mean()
            if result > limite:
                parar = True
                result2 = result
        i += 1
    return idx_b,result2

In [53]:
def selectBestForward2(num_feat,sbs_model,X,y,idx,models,limite):
    X_train = X[:,idx]
    i = 1
    parar = False
    result2 = 0
    while i < num_feat and parar==False:
        startTime = time.time()
        svm_b = SFS(sbs_model,
            k_features=i,
            forward=True,
            floating=True,
            verbose=0,
            scoring='accuracy',
            cv=0,
            n_jobs=1)
        svm_b = svm_b.fit(X_train,y,custom_feature_names=idx)
        idx_b = svm_b.k_feature_names_
        endTimeSFS = time.time()
        timeUsedSFS = timedelta(seconds=endTimeSFS-startTime)
        print('- Time used in SFS iteration ' + str(i) +': ' + str(timeUsedSFS))
        print(str(len(idx_b)))
        X_sbs = X[:,idx_b]
        for model in models:
            cv = cross_validate(model,X_sbs,y,cv=5,return_train_score=True)
            result = cv['test_score'].mean()
            if result > limite:
                parar = True
                result2 = result
        i += 1
    return idx_b,result2


In [2]:
def printBestResult(myDf):
    maxAccuracy = myDf[0]['Test'].idxmax()
    maxPrecision = myDf[1]['Test'].idxmax()
    maxRecall = myDf[2]['Test'].idxmax()
    print('- Max Accuracy:   ' + str(myDf[0].loc[maxAccuracy,'Test'])  + ' using: ' + str(maxAccuracy)  + ' attributes.')
    print('- Max Precission: ' + str(myDf[1].loc[maxPrecision,'Test']) + ' using: ' + str(maxPrecision) + ' attributes.')
    print('- Max Recall:     ' + str(myDf[2].loc[maxRecall,'Test'])    + ' using: ' + str(maxRecall)    + ' attributes.')
    

def printTotalBestResult(KNNdf,DTCdf,SVCdf):
    print('KNN')
    printBestResult(KNNdf)

    print('\nDTC')
    printBestResult(DTCdf)
    
    print('\nSVC')
    printBestResult(SVCdf)

In [3]:
def hybrid_model_result(X_train,X_test,y_train,y_test,model,num_fea,scoring,idx):
    modelResult = []
    modelTime = []
    myResult = []
    
    c_matrix = []
    
    knn_modelResult_acc = []
    knn_modelResult_prec = []
    knn_modelResult_rec = []
    knn_modelResult_time = []

    dtc_modelResult_acc = []
    dtc_modelResult_prec = []
    dtc_modelResult_rec = []
    dtc_modelResult_time = []
    
    svc_modelResult_acc = []
    svc_modelResult_prec = []
    svc_modelResult_rec = []
    svc_modelResult_time = []

    for i in range(0,len(model)):
        acc,prec,rec,modelTime,cMatrix = train_ml_method(X_train,X_test,y_train,y_test,num_fea,model[i],scoring,idx)
        c_matrix.append(cMatrix)
        if i == 0:
            knn_modelResult_acc.append(acc)
            knn_modelResult_prec.append(prec)
            knn_modelResult_rec.append(rec)
            knn_modelResult_time.append(modelTime)
        if i == 1:
            dtc_modelResult_acc.append(acc)
            dtc_modelResult_prec.append(prec)
            dtc_modelResult_rec.append(rec)
            dtc_modelResult_time.append(modelTime)
        if i == 2:
            svc_modelResult_acc.append(acc)
            svc_modelResult_prec.append(prec)
            svc_modelResult_rec.append(rec)
            svc_modelResult_time.append(modelTime)

    knn_results = [knn_modelResult_acc,knn_modelResult_prec,knn_modelResult_rec,knn_modelResult_time]
    dtc_results = [dtc_modelResult_acc,dtc_modelResult_prec,dtc_modelResult_rec,dtc_modelResult_time]
    svc_results = [svc_modelResult_acc,svc_modelResult_prec,svc_modelResult_rec,svc_modelResult_time]
    model_cmatrix = [c_matrix]
    return knn_results,dtc_results,svc_results,model_cmatrix

In [4]:
def model_result(X,y,crossVal,model,num_fea,scoring,fs_method):
    modelResult = []
    modelTime = []
    myResult = []
    totalTimeFS = 0
    
    c_matrix = []
    
    knn_modelResult_acc = []
    knn_modelResult_prec = []
    knn_modelResult_rec = []
    knn_modelResult_time = []

    dtc_modelResult_acc = []
    dtc_modelResult_prec = []
    dtc_modelResult_rec = []
    dtc_modelResult_time = []
    
    svc_modelResult_acc = []
    svc_modelResult_prec = []
    svc_modelResult_rec = []
    svc_modelResult_time = []

    k = 0
    for train_index,test_index in crossVal.split(X,y):
        startFS = time.time()    
        X_train, X_test = X[train_index],X[test_index]
        y_train, y_test = y[train_index],y[test_index]
        # FS method selection
        idx = select_FS_method(fs_method,X_train,y_train,num_fea)
        endFS = time.time()
        timeUsed = timedelta(seconds=endFS-startFS)
        print('- Time used in iteration ' + str(k) + ' for FS: '  + str(timeUsed))
        # end - FS method
        totalTimeFS = totalTimeFS + endFS - startFS
        '''
        for models in model:
            #modelResult.append(train_ml_method(X_train,X_test,y_train,y_test,num_fea,models,scoring,idx))
        '''
        for i in range(0,len(model)):
            acc,prec,rec,modelTime,cMatrix = train_ml_method(X_train,X_test,y_train,y_test,num_fea,model[i],scoring,idx)
            c_matrix.append(cMatrix)
            if i == 0:
                knn_modelResult_acc.append(acc)
                knn_modelResult_prec.append(prec)
                knn_modelResult_rec.append(rec)
                knn_modelResult_time.append(modelTime)
            if i == 1:
                dtc_modelResult_acc.append(acc)
                dtc_modelResult_prec.append(prec)
                dtc_modelResult_rec.append(rec)
                dtc_modelResult_time.append(modelTime)
            if i == 2:
                svc_modelResult_acc.append(acc)
                svc_modelResult_prec.append(prec)
                svc_modelResult_rec.append(rec)
                svc_modelResult_time.append(modelTime)
        endFold = time.time()
        time_fold = timedelta(seconds=endFold-startFS)
        print('------- Time used in FOLD ' + str(k) + ':       '  + str(time_fold))
        k += 1

    knn_results = [knn_modelResult_acc,knn_modelResult_prec,knn_modelResult_rec,knn_modelResult_time]
    dtc_results = [dtc_modelResult_acc,dtc_modelResult_prec,dtc_modelResult_rec,dtc_modelResult_time]
    svc_results = [svc_modelResult_acc,svc_modelResult_prec,svc_modelResult_rec,svc_modelResult_time]
    model_cmatrix = [c_matrix]
    totalTimeFS = timedelta(seconds=totalTimeFS)
    print('- TOTAL TIME IN FS: ' + str(totalTimeFS))
    return knn_results,dtc_results,svc_results,model_cmatrix

In [5]:
def model_result2(X,y,crossVal,model,num_fea,scoring,idx):
    modelResult = []
    modelTime = []
    myResult = []
    totalTimeFS = 0
    
    c_matrix = []
    
    knn_modelResult_acc = []
    knn_modelResult_prec = []
    knn_modelResult_rec = []
    knn_modelResult_time = []

    dtc_modelResult_acc = []
    dtc_modelResult_prec = []
    dtc_modelResult_rec = []
    dtc_modelResult_time = []
    
    svc_modelResult_acc = []
    svc_modelResult_prec = []
    svc_modelResult_rec = []
    svc_modelResult_time = []

    k = 0
    for train_index,test_index in crossVal.split(X,y):
        startFS = time.time()    
        X_train, X_test = X[train_index],X[test_index]
        y_train, y_test = y[train_index],y[test_index]
        for i in range(0,len(model)):
            acc,prec,rec,modelTime,cMatrix = train_ml_method(X_train,X_test,y_train,y_test,num_fea,model[i],scoring,idx)
            c_matrix.append(cMatrix)
            if i == 0:
                knn_modelResult_acc.append(acc)
                knn_modelResult_prec.append(prec)
                knn_modelResult_rec.append(rec)
                knn_modelResult_time.append(modelTime)
            if i == 1:
                dtc_modelResult_acc.append(acc)
                dtc_modelResult_prec.append(prec)
                dtc_modelResult_rec.append(rec)
                dtc_modelResult_time.append(modelTime)
            if i == 2:
                svc_modelResult_acc.append(acc)
                svc_modelResult_prec.append(prec)
                svc_modelResult_rec.append(rec)
                svc_modelResult_time.append(modelTime)
        endFold = time.time()
        time_fold = timedelta(seconds=endFold-startFS)
        print('------- Time used in FOLD ' + str(k) + ':       '  + str(time_fold))
        k += 1

    knn_results = [knn_modelResult_acc,knn_modelResult_prec,knn_modelResult_rec,knn_modelResult_time]
    dtc_results = [dtc_modelResult_acc,dtc_modelResult_prec,dtc_modelResult_rec,dtc_modelResult_time]
    svc_results = [svc_modelResult_acc,svc_modelResult_prec,svc_modelResult_rec,svc_modelResult_time]
    model_cmatrix = [c_matrix]
    totalTimeFS = timedelta(seconds=totalTimeFS)
    print('- TOTAL TIME IN FS: ' + str(totalTimeFS))
    return knn_results,dtc_results,svc_results,model_cmatrix

In [6]:
def select_FS_method(fs_method,X_train,y_train,num_fea):
    if fs_method == 'f_score':
        score = f_score.f_score(X_train,y_train)
        idx = f_score.feature_ranking(score)
    elif fs_method == 'mrmr':
        idx = MRMR.mrmr(X_train,y_train,n_selected_features=num_fea)
    elif fs_method == 'svm_f':
        clf_SVC = SVC()
        svm_f = SFS(clf_SVC,k_features=num_fea,forward=True,floating=False,verbose=1,scoring='accuracy',cv=0,n_jobs=1)
        svm_f = svm_f.fit(X_train,y_train)
        idx = svm_f.k_feature_idx_
    elif fs_method == 'svm_b':
        clf_SVC = SVC()
        svm_f = SFS(clf_SVC,k_features=num_fea,forward=False,floating=False,verbose=1,scoring='accuracy',cv=0,n_jobs=1)
        svm_f = svm_f.fit(X_train,y_train)
        idx = svm_f.k_feature_idx_
    return idx

In [7]:
def train_ml_method(X_train,X_test,y_train,y_test,num_fea,model,scoring,idx):
    startMl = time.time()
    modelResultAcc = []
    modelResultPrec = []
    modelResultRec = []
    conf_matrix = []
    modelTime = []
    for i in range(1,num_fea+1):
        train_sf = X_train[:,idx[0:i]]
        test_sf = X_test[:,idx[0:i]]
        cv = cross_validate(model,train_sf,y_train,cv=5,scoring=scoring,return_train_score=True)
        start = time.time()
        model.fit(train_sf,y_train)
        # acc,prec,rec
        myPredict = model.predict(test_sf)
        test_acc_score = accuracy_score(y_test,myPredict)
        test_prec_score = precision_score(y_test,myPredict)
        test_rec_score = recall_score(y_test,myPredict)
        test_conf_matrix = confusion_matrix(y_test,myPredict)
        #test_score = model.score(test_sf,y_test)
        end = time.time()
        modelResultAcc.append([cv['train_accuracy'].mean(),cv['test_accuracy'].mean(),test_acc_score])
        modelResultPrec.append([cv['train_precision'].mean(),cv['test_precision'].mean(),test_prec_score])
        modelResultRec.append([cv['train_recall'].mean(),cv['test_recall'].mean(),test_rec_score])
        modelTime.append([cv['fit_time'].mean()+cv['score_time'].mean(),end-start])
        conf_matrix.append(test_conf_matrix)
    endMl = time.time()
    totalTime = timedelta(seconds=endMl-startMl)
    print('         - Time used in ' + str(model)[0:10] + ' ' + str(totalTime))
    return modelResultAcc, modelResultPrec, modelResultRec, modelTime,conf_matrix

In [8]:
def getResults(myArray):
    myResults = []
    for i in range(0,len(myArray)):
        df_to_return = pd.DataFrame(myArray[i][0])
        for j in range(1,len(myArray[i])):
            df_aux = pd.DataFrame(myArray[i][j])
            df_to_return += df_aux
        df_to_return /= len(myArray[i])
        myResults.append(df_to_return)
    return myResults

In [9]:
def formatArray(myArray):
    df = getResults(myArray)
    n_samples,n_features = df[0].shape
    index_list = list(np.arange(1,n_samples+1))
    columnName = ['Train','Validate','Test']
    columnName2 = ['Train_Time','Test_Time']
    
    for i in range(0,len(df)):
        df[i].index = index_list
        if i!=3:
            df[i].columns = columnName
        else:
            df[i].columns = columnName2
    return df
    

In [10]:
def plotModel(myDf):

    fig, axes = plt.subplots(nrows=4, ncols=1, figsize=(15,25))

    a0 = myDf[0].plot(ax=axes[0],grid=True)
    axes[0].set_title('Accuracy')
    a0.set_xlabel('num of attributes used')
    a0.set_ylabel('Accuracy')

    a1 = myDf[1].plot(ax=axes[1],grid=True)
    axes[1].set_title('Precision')
    a1.set_xlabel('num of attributes used')
    a1.set_ylabel('Precision')

    a2 = myDf[2].plot(ax=axes[2],grid=True)
    axes[2].set_title('Recall')
    a2.set_xlabel('num of attributes used')
    a2.set_ylabel('Recall')

    a3 = myDf[3].plot(ax=axes[3],grid=True)
    axes[3].set_title('Time')
    a3.set_xlabel('num of attributes used')
    a3.set_ylabel('Time')

    plt.subplots_adjust(hspace=0.3)

    plt.show()


In [11]:
def plotModel2(myDf1,myDf2,myDf3,figsize,wspace,hspace,fontsize):

    #fig, axes = plt.subplots(nrows=4, ncols=3, figsize=(15,15))
    fig, axes = plt.subplots(nrows=4, ncols=3, figsize=figsize)
    
    #KNN
    a0 = myDf1[0].plot(ax=axes[0,0],grid=True, fontsize=fontsize)
    axes[0,0].set_title('KNN Accuracy',fontsize=1.5*fontsize)
    a0.legend(fontsize=fontsize,loc=4)
    a0.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    a0.set_ylabel('Accuracy',fontsize=1.25*fontsize)

    a1 = myDf1[1].plot(ax=axes[1,0],grid=True, fontsize=fontsize)
    axes[1,0].set_title('KNN Precision',fontsize=1.5*fontsize)
    a1.legend(fontsize=fontsize,loc=4)
    a1.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    a1.set_ylabel('Precision',fontsize=1.25*fontsize)

    a2 = myDf1[2].plot(ax=axes[2,0],grid=True, fontsize=fontsize)
    axes[2,0].set_title('KNN Recall',fontsize=1.5*fontsize)
    a2.legend(fontsize=fontsize,loc=4)
    a2.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    a2.set_ylabel('Recall',fontsize=1.25*fontsize)

    a3 = myDf1[3].plot(ax=axes[3,0],grid=True, fontsize=fontsize)
    axes[3,0].set_title('KNN Time',fontsize=1.5*fontsize)
    a3.legend(fontsize=fontsize,loc=4)
    a3.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    a3.set_ylabel('Time',fontsize=1.25*fontsize)

    #DTC
    b0 = myDf2[0].plot(ax=axes[0,1],grid=True, fontsize=fontsize)
    axes[0,1].set_title('DTC Accuracy',fontsize=1.5*fontsize)
    b0.legend(fontsize=fontsize,loc=4)
    b0.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    b0.set_ylabel('Accuracy',fontsize=1.25*fontsize)

    b1 = myDf2[1].plot(ax=axes[1,1],grid=True, fontsize=fontsize)
    axes[1,1].set_title('DTC Precision',fontsize=1.5*fontsize)
    b1.legend(fontsize=fontsize,loc=4)
    b1.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    b1.set_ylabel('Precision',fontsize=1.25*fontsize)

    b2 = myDf2[2].plot(ax=axes[2,1],grid=True, fontsize=fontsize)
    axes[2,1].set_title('DTC Recall',fontsize=1.5*fontsize)
    b2.legend(fontsize=fontsize,loc=4)
    b2.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    b2.set_ylabel('Recall',fontsize=1.25*fontsize)

    b3 = myDf2[3].plot(ax=axes[3,1],grid=True, fontsize=fontsize)
    axes[3,1].set_title('DTC Time',fontsize=1.5*fontsize)
    b3.legend(fontsize=fontsize,loc=4)
    b3.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    b3.set_ylabel('Time',fontsize=1.25*fontsize)

    #SVC
    c0 = myDf3[0].plot(ax=axes[0,2],grid=True, fontsize=fontsize)
    axes[0,2].set_title('SVC Accuracy',fontsize=1.5*fontsize)
    c0.legend(fontsize=fontsize,loc=4)
    c0.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    c0.set_ylabel('Accuracy',fontsize=1.25*fontsize)

    c1 = myDf3[1].plot(ax=axes[1,2],grid=True, fontsize=fontsize)
    axes[1,2].set_title('SVC Precision',fontsize=1.5*fontsize)
    c1.legend(fontsize=fontsize,loc=4)
    c1.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    c1.set_ylabel('Precision',fontsize=1.25*fontsize)

    c2 = myDf3[2].plot(ax=axes[2,2],grid=True, fontsize=fontsize)
    axes[2,2].set_title('SVC Recall',fontsize=1.5*fontsize)
    c2.legend(fontsize=fontsize,loc=4)
    c2.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    c2.set_ylabel('Recall',fontsize=1.25*fontsize)

    c3 = myDf3[3].plot(ax=axes[3,2],grid=True, fontsize=fontsize)
    axes[3,2].set_title('SVC Time',fontsize=1.5*fontsize)
    c3.legend(fontsize=fontsize,loc=4)
    c3.set_xlabel('num of attributes used',fontsize=1.25*fontsize)
    c3.set_ylabel('Time',fontsize=1.25*fontsize)
    
    
    #PRINT
    #plt.subplots_adjust(wspace=0.3, hspace=0.3)
    plt.subplots_adjust(wspace=wspace, hspace=hspace)

    plt.show()
    
    fig.savefig('pdf_testplot.pdf')
    fig.savefig('jpg_testplot.jpg',quality=95)


In [12]:
def plot_confusion_matrix(cm,
                          target_names,
                          title='Confusion matrix',
                          cmap=None,
                          normalize=True):
    """
    given a sklearn confusion matrix (cm), make a nice plot

    Arguments
    ---------
    cm:           confusion matrix from sklearn.metrics.confusion_matrix

    target_names: given classification classes such as [0, 1, 2]
                  the class names, for example: ['high', 'medium', 'low']

    title:        the text to display at the top of the matrix

    cmap:         the gradient of the values displayed from matplotlib.pyplot.cm
                  see http://matplotlib.org/examples/color/colormaps_reference.html
                  plt.get_cmap('jet') or plt.cm.Blues

    normalize:    If False, plot the raw numbers
                  If True, plot the proportions

    Usage
    -----
    plot_confusion_matrix(cm           = cm,                  # confusion matrix created by
                                                              # sklearn.metrics.confusion_matrix
                          normalize    = True,                # show proportions
                          target_names = y_labels_vals,       # list of names of the classes
                          title        = best_estimator_name) # title of graph

    Citiation
    ---------
    http://scikit-learn.org/stable/auto_examples/model_selection/plot_confusion_matrix.html

    """
    import matplotlib.pyplot as plt
    import numpy as np
    import itertools

    accuracy = np.trace(cm) / float(np.sum(cm))
    misclass = 1 - accuracy

    if cmap is None:
        cmap = plt.get_cmap('Blues')

    plt.figure(figsize=(8, 6))
    plt.imshow(cm, interpolation='nearest', cmap=cmap)
    plt.title(title)
    plt.colorbar()

    if target_names is not None:
        tick_marks = np.arange(len(target_names))
        plt.xticks(tick_marks, target_names, rotation=45)
        plt.yticks(tick_marks, target_names)

    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]


    thresh = cm.max() / 1.5 if normalize else cm.max() / 2
    for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        if normalize:
            plt.text(j, i, "{:0.4f}".format(cm[i, j]),
                     horizontalalignment="center",
                     color="white" if cm[i, j] > thresh else "black")
        else:
            plt.text(j, i, "{:,}".format(cm[i, j]),
                     horizontalalignment="center",
                     color="white" if cm[i, j] > thresh else "black")


    plt.tight_layout()
    plt.ylabel('True label')
    plt.xlabel('Predicted label\naccuracy={:0.4f}; misclass={:0.4f}'.format(accuracy, misclass))
    plt.show()